In [47]:
import pandas as pd
from pandas import DataFrame
from ydata_profiling import ProfileReport
from datetime import datetime
import glob
import os

# Data from .csv files


In [48]:
def rename_columns(df: DataFrame) -> DataFrame:
    """
    rename_columns function renames columns in the DataFrame for consistency and clarity.

    Args:
        df (DataFrame): The DataFrame containing the data with original column names.

    Returns:
        DataFrame: A DataFrame with renamed columns.

    """
    # The original column names are in Thai and some are not consistent across different years.
    renamed_col_dict: dict = {
        "Dead Conso Id": "id",
        "Dead Year_ปีที่เสียชีวิต ": "DeadYear_BE",
        "DEAD_YEAR": "DeadYear_AD",
        "Age": "Age",
        "Sex": "Sex",
        "Nationality Id": "Nationality",
        "Tumbol": "SubDist",
        "District": "District",
        "Province": "Province",
        "Risk Helmet": "RiskHelmet",
        "Risk Safety Belt": "RiskSafetyBelt",
        "Dead Date Final": "DeadDate",
        "Date Rec": "DateRec",
        "Time Rec": "TimeRec",
        "Acc Sub Dist": "AccSubDist",
        "Acc Dist": "AccDistrict",
        "จ.ที่เสียชีวิต": "AccProvince",
        "Acc La": "AccLat",
        "Acclong": "AccLong",
        "Ncause": "ICD_10",
        "Vehicle Merge Final": "Vehicle",
    }

    df.rename(columns=renamed_col_dict, inplace=True)
    return df

In [ ]:
pd.Int64Dtype()

Int64Dtype()

In [103]:
from pandas import Int64Dtype


def correct_dtype(df: DataFrame) -> DataFrame:
    """
    correct_dtype function corrects the data types of specific columns in the DataFrame for better profiling.

    Args:
        df (DataFrame): The DataFrame containing the data with data type.

    Returns:
        DataFrame: A DataFrame with corrected data types.
    """
    # correcting data types for better profiling
    corrected_dtype: dict = {
        "id": "int",
        "DeadYear_BE": "Int64",
        "DeadYear_AD": "Int64",
        "Age": "Int64",
        "Sex": "category",
        "Nationality": "category",
        "SubDist": "category",
        "District": "category",
        "Province": "category",
        "RiskHelmet": "Int64",
        "RiskSafetyBelt": "Int64",
        "AccSubDist": "category",
        "AccDistrict": "category",
        "AccProvince": "category",
        "ICD_10": "category",
        "Vehicle": "category",
    }

    df = df.astype(corrected_dtype)
    return df

In [90]:
def load_and_concatenate_csv_files() -> DataFrame:
    """
    load_and_concatenate_csv_files

    Returns:

    """
    """
    load_and_concatenate_csv_files function loads and concatenates multiple CSV files from the 'data' directory.

    Raises:
        FileNotFoundError: If the 'data' directory does not exist.
        NotADirectoryError: If the 'data' path is not a directory.    

    Returns:
        DataFrame: A pandas DataFrame containing the concatenated data from all CSV files.
    """
    # Ensure the 'data' directory exists
    data_directory = "data"

    if not os.path.exists(data_directory):
        raise FileNotFoundError(f"The directory '{data_directory}' does not exist.")
    # Ensure the 'data' directory is a directory
    if not os.path.isdir(data_directory):
        raise NotADirectoryError(f"The path '{data_directory}' is not a directory.")

    # Get all CSV file paths in the data directory
    csv_files = glob.glob(r"data\*.csv")
    csv_files.sort()  # Sort files to ensure consistent order

    if not csv_files:
        raise FileNotFoundError("No CSV files found in the 'data' directory.")

    # Load and concatenate all CSV files into a single DataFrame
    # The first 13 files are encoded in "cp874" for Thai charactors and the last 2 files are in default encoding (UTF-8).
    df_54to66: DataFrame = pd.concat(
        [pd.read_csv(file_path, encoding="cp874") for file_path in csv_files[:13]],
        ignore_index=True,
    )
    df_67to68: DataFrame = pd.concat(
        [pd.read_csv(file_path) for file_path in csv_files[13:]], ignore_index=True
    )
    # If the CSV files have different columns, this will result in NaN values for missing columns in some files.
    # Ensure that the columns are consistent across all files.
    if not df_54to66.columns.equals(df_67to68.columns):
        raise ValueError("CSV files have inconsistent columns.")

    # Concatenate the two DataFrames
    df: DataFrame = pd.concat(objs=[df_54to66, df_67to68], ignore_index=True)
    print(csv_files)

    print(
        f"\nConcatenated DataFrame shape: {df.shape[0]:,} rows {df.shape[1]} columns\n"
    )
    # drop rows with all NaN values
    df.dropna(how="all", inplace=True)
    print("Removed rows with all NaN values.")
    print(f" - Total rows after dropping NaN rows: {len(df):,}\n")
    # rename columns for consistency
    df = rename_columns(df)
    print("Renamed columns and corrected data types.\n")
    # correct data types for better profiling
    df = correct_dtype(df)
    print("Completed loading and concatenating CSV files.\n")
    return df

In [80]:
def create_profile_report(
    df: DataFrame, report_title: str = "Thai Traffic Deaths EDA report"
) -> ProfileReport:
    """
    create_profile_report function generates a profile report for the given DataFrame and save the report to output folder.

    Args:
        df (DataFrame): The DataFrame to be profiled.
        title (str): The title of the profile report.

    Returns:
        ProfileReport: A profile report object.
    """
    # make sure the output directory exists
    import os

    if not os.path.exists("output"):
        os.makedirs("output")

    # output file configuration
    SAVE_NAME = "traffic_death_eda_report"
    SAVE_DATE = datetime.now().strftime("%Y-%m-%d %H:%M:%S").split(" ")[0]
    SAVE_DIR = r"output"
    OUTPUT_PATH = f"{SAVE_DIR}/{SAVE_NAME}_{SAVE_DATE}.html"

    # Generate the profiling report
    report = ProfileReport(
        df,
        title=report_title,
        explorative=True,
    )
    # Save the report to an HTML file
    report.to_file(OUTPUT_PATH)
    print(f"Profile report saved to {OUTPUT_PATH}")
    return report

In [104]:
df = load_and_concatenate_csv_files()

['data\\_2554.csv', 'data\\_2555.csv', 'data\\_2556.csv', 'data\\_2557.csv', 'data\\_2558.csv', 'data\\_2559.csv', 'data\\_2560.csv', 'data\\_2561.csv', 'data\\_2562.csv', 'data\\_2563.csv', 'data\\_2564.csv', 'data\\_2565.csv', 'data\\_2566.csv', 'data\\_2567.csv', 'data\\_2568.csv']

Concatenated DataFrame shape: 293,376 rows 21 columns

Removed rows with all NaN values.
 - Total rows after dropping NaN rows: 280,140

Renamed columns and corrected data types.

Completed loading and concatenating CSV files.



In [105]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 280140 entries, 0 to 280139
Data columns (total 21 columns):
 #   Column          Non-Null Count   Dtype   
---  ------          --------------   -----   
 0   id              280140 non-null  int64   
 1   DeadYear_BE     280140 non-null  Int64   
 2   DeadYear_AD     280140 non-null  Int64   
 3   Age             249879 non-null  Int64   
 4   Sex             280138 non-null  category
 5   Nationality     146651 non-null  category
 6   SubDist         34258 non-null   category
 7   District        101586 non-null  category
 8   Province        101768 non-null  category
 9   RiskHelmet      4390 non-null    Int64   
 10  RiskSafetyBelt  2066 non-null    Int64   
 11  DeadDate        280140 non-null  object  
 12  DateRec         106950 non-null  object  
 13  TimeRec         106950 non-null  object  
 14  AccSubDist      129718 non-null  category
 15  AccDistrict     142452 non-null  category
 16  AccProvince     280140 non-null  category
 

In [106]:
df.nunique()

id                280140
DeadYear_BE           15
DeadYear_AD           15
Age                  118
Sex                    3
Nationality          101
SubDist             5485
District             990
Province             155
RiskHelmet             3
RiskSafetyBelt         3
DeadDate            5204
DateRec             4018
TimeRec             1440
AccSubDist          5967
AccDistrict         1117
AccProvince           78
AccLat            115751
AccLong           114211
ICD_10               375
Vehicle               10
dtype: int64

In [107]:
df.Nationality.unique().tolist()

[99.0,
 nan,
 71.0,
 208.0,
 25.0,
 56.0,
 82.0,
 9.0,
 45.0,
 198.0,
 44.0,
 48.0,
 199.0,
 36.0,
 57.0,
 72.0,
 38.0,
 96.0,
 30.0,
 98.0,
 258.0,
 49.0,
 126.0,
 259.0,
 46.0,
 'Thai',
 'Lao Laotian',
 'Cambodian',
 'Burmese',
 'German',
 'Belarusian',
 'Norwegian',
 'Danish Dane',
 'Bahamian',
 'Beninese',
 'Israeli',
 'Malian',
 'Ecuadorian',
 'American',
 'Japanese',
 'Dutch Dutchman',
 'Afghan',
 'Bahraini',
 'Bruneian',
 'Romanian',
 'Macedonian',
 'Yemeni',
 'Colombian',
 'Icelander',
 'Malawian',
 'Australian',
 'British Briton',
 'Chinese',
 'Swazi',
 'Malaysian',
 'Comoran',
 'Austrian',
 'Ukrainian',
 'Italian',
 'Iranian',
 'Russian',
 'French',
 'Vietnamese',
 'Cuban',
 'Belgian',
 'Swedish Swede',
 'Bosnian Herzegovinian',
 'Polish Pole',
 'Burundian',
 'Lithuanian',
 'British/Briton',
 'Lao, Laotian',
 'Filipino',
 'Bermudan',
 'Dutch/Dutchman',
 'Kazakhstani',
 'Irish/Irishman',
 'Tanzanian',
 'Polish/Pole',
 'Swedish/Swede',
 'Singaporean',
 'Swiss',
 'Gibraltarian',

In [108]:
for col in df.columns:
    if (df[col].nunique() <= 120) and (df[col].isnull().sum() != len(df[col])):
        print("\n")
        print(df[col].value_counts(dropna=False, sort=False))



DeadYear_BE
2554    21996
2555    21603
2556    21221
2557    20790
2558    19960
2559    21745
2560    21607
2561    19931
2562    19904
2563    17831
2564    16957
2565    17379
2566    17498
2567    17477
2568     4241
Name: count, dtype: Int64


DeadYear_AD
2011    21996
2012    21603
2013    21221
2014    20790
2015    19960
2016    21745
2017    21607
2018    19931
2019    19904
2020    17831
2021    16957
2022    17379
2023    17498
2024    17477
2025     4241
Name: count, dtype: Int64


Age
38       3886
41       3750
54       3771
79       1014
42       3845
        ...  
110         1
100         1
154         1
122         1
<NA>    30261
Name: count, Length: 119, dtype: Int64


Sex
ชาย        214236
หญิง        59338
ไม่ระบุ      6564
NaN             2
Name: count, dtype: int64


Nationality
9.0                2
25.0               1
30.0               1
36.0              11
38.0               2
               ...  
Ugandan            1
Ukrainian          3
Vietnamese     

In [109]:
eda_report = create_profile_report(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 21/21 [01:17<00:00,  3.70s/it]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3594 (\N{THAI CHARACTER CHO CHANG}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3634 (\N{THAI CHARACTER SARA AA}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3618 (\N{THAI CHARACTER YO YAK}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3627 (\N{THAI CHARACTER HO HIP}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3597 (\N{THAI CHARACTER YO YING}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\s

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Profile report saved to output/traffic_death_eda_report_2025-07-17.html


In [110]:
eda_report

-----------------

# Data from .xlsx files

In [2]:
DATA_PATH = r"D:\repos\thai_traffic_deaths\data\traffic_death.xlsx"

df = pd.read_excel(
    DATA_PATH,
)

df.head()

id  DEAD_YEAR(Budha)  DEAD_YEAR Age  Sex  BirthYear  NationalityId  \
0  8635072              2555       2012  18  1.0        NaN           99.0   
1  8635074              2555       2012  18  1.0        NaN           99.0   
2  8635084              2555       2012  21  1.0        NaN           99.0   
3  8640055              2555       2012  58  1.0        NaN           99.0   
4  8634703              2555       2012   4  1.0        NaN           99.0   

   Tumbol  District  Province  ...   DeadDate  DateRec TimeRec AccSubDist  \
0     NaN       NaN       NaN  ... 2012-12-16      NaT     NaN        NaN   
1     NaN       NaN       NaN  ... 2012-05-27      NaT     NaN        NaN   
2     NaN       NaN       NaN  ... 2012-05-01      NaT     NaN        NaN   
3     NaN       NaN       NaN  ... 2012-02-03      NaT     NaN        NaN   
4     NaN       NaN       NaN  ... 2012-12-11      NaT     NaN        NaN   

   AccDist   AccProv AccLat Acclong  ICD-10        Vehicle  
0      NaN  สุรินทร์    NaN     NaN    V284  รถจักรยานยนต์  
1      NaN  สุรินทร์    NaN     NaN    V892   ไม่ระบุพาหนะ  
2      NaN  สุรินทร์    NaN     NaN    V892   ไม่ระบุพาหนะ  
3      NaN  สุรินทร์    NaN     NaN    V892   ไม่ระบุพาหนะ  
4      NaN  ศรีสะเกษ    NaN     NaN    V846   ไม่ระบุพาหนะ  

[5 rows x 22 columns]

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 215389 entries, 0 to 215388
Data columns (total 22 columns):
 #   Column            Non-Null Count   Dtype         
---  ------            --------------   -----         
 0   id                215389 non-null  int64         
 1   DEAD_YEAR(Budha)  215389 non-null  int64         
 2   DEAD_YEAR         215389 non-null  int64         
 3   Age               215389 non-null  object        
 4   Sex               211286 non-null  float64       
 5   BirthYear         0 non-null       float64       
 6   NationalityId     119233 non-null  float64       
 7   Tumbol            0 non-null       float64       
 8   District          0 non-null       float64       
 9   Province          0 non-null       float64       
 10  RiskHelmet        0 non-null       float64       
 11  RiskSafetyBelt    0 non-null       float64       
 12  DeadDate          215389 non-null  datetime64[ns]
 13  DateRec           102745 non-null  datetime64[ns]
 14  Time

In [9]:
for col in df.columns:
    if (df[col].nunique() <= 50) and (df[col].isnull().sum() != len(df[col])):
        print("\n")
        print(df[col].value_counts(dropna=False))



Dead Year_ปีที่เสียชีวิต 
2554.0    21996
2559.0    21745
2560.0    21607
2555.0    21603
2556.0    21221
2557.0    20790
2558.0    19960
2561.0    19931
2562.0    19904
2563.0    17831
2566.0    17498
2567.0    17477
2565.0    17379
2564.0    16957
NaN       13236
2568.0     4241
Name: count, dtype: int64


DEAD_YEAR
2011.0    21996
2016.0    21745
2017.0    21607
2012.0    21603
2013.0    21221
2014.0    20790
2015.0    19960
2018.0    19931
2019.0    19904
2020.0    17831
2023.0    17498
2024.0    17477
2022.0    17379
2021.0    16957
NaN       13236
2025.0     4241
Name: count, dtype: int64


Sex
ชาย        214236
หญิง        59338
NaN         13238
ไม่ระบุ      6564
Name: count, dtype: int64


Risk Helmet
NaN    288986
2.0      3048
1.0      1121
3.0       221
Name: count, dtype: int64


Risk Safety Belt
NaN    291310
2.0      1363
3.0       625
1.0        78
Name: count, dtype: int64


Vehicle Merge Final
ไม่ระบุพาหนะ              129689
รถจักรยานยนต์             114292
รถยนต์ 

In [5]:
# correcting data types for better profiling
corrected_dtype: dict = {
    "id": "int",
    "DEAD_YEAR(Budha)": "category",
    "DEAD_YEAR": "category",
    "Age": "category",
    "Sex": "category",
    "NationalityId": "category",
    "AccSubDist": "category",
    "AccDist": "category",
    "AccProv": "category",
    "ICD-10": "category",
    "Vehicle": "category",
}

df = df.astype(corrected_dtype)

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 215389 entries, 0 to 215388
Data columns (total 22 columns):
 #   Column            Non-Null Count   Dtype         
---  ------            --------------   -----         
 0   id                215389 non-null  int64         
 1   DEAD_YEAR(Budha)  215389 non-null  category      
 2   DEAD_YEAR         215389 non-null  category      
 3   Age               215389 non-null  category      
 4   Sex               211286 non-null  category      
 5   BirthYear         0 non-null       float64       
 6   NationalityId     119233 non-null  category      
 7   Tumbol            0 non-null       float64       
 8   District          0 non-null       float64       
 9   Province          0 non-null       float64       
 10  RiskHelmet        0 non-null       float64       
 11  RiskSafetyBelt    0 non-null       float64       
 12  DeadDate          215389 non-null  datetime64[ns]
 13  DateRec           102745 non-null  datetime64[ns]
 14  Time

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3652 (\N{THAI CHARACTER SARA AI MAIMALAI}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3617 (\N{THAI CHARACTER MO MA}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3656 (\N{THAI CHARACTER MAI EK}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3619 (\N{THAI CHARACTER RO RUA}) missing from font(s) Arial.
  plt.savefig(
d:\repos\thai_traffic_deaths\.venv\Lib\site-packages\ydata_profiling\visualisation\utils.py:73: UserWarning: Glyph 3632 (\N{THAI CHARACTER SARA A}) missing from fo